In [2]:
import ee
import geemap
import folium
import tqdm
import pandas as pd
import numpy as np
import geopandas as gpd
from shapely.geometry import Point, Polygon


In [4]:
Map = geemap.Map()

In [56]:
# Define the area of interest and date range
davis = ee.Geometry.Point([-121.7405, 38.5449])  # Longitude, Latitude of Davis, CA
start_date = '2016-01-01'
end_date = '2023-12-31'


In [60]:
# Load Sentinel-1 and 2 imagery
sentinel_1 = ee.ImageCollection('COPERNICUS/S1_GRD')\
    .filterDate(start_date, end_date)\
    .filter(ee.Filter.eq('instrumentMode', 'IW'))\
    .filter(ee.Filter.listContains('transmitterReceiverPolarisation', 'VV'))\
    .filter(ee.Filter.listContains('transmitterReceiverPolarisation', 'VH'))

sentinel_2 = ee.ImageCollection("COPERNICUS/S2_HARMONIZED")\
    .filterDate(start_date, end_date)\
    .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 5))

# SMAP Soil Moisture
smap = ee.ImageCollection("NASA/SMAP/SPL3SMP_E/005")\
    .filterDate(start_date, end_date)\
    .select('soil_moisture_am')

# Landsat Thermal
landsat_8 = ee.ImageCollection("LANDSAT/LC08/C02/T1_TOA")\
    .filterDate(start_date, end_date)\
    .select(['B10', 'B11'])\
    .filter(ee.Filter.lt('CLOUD_COVER', 5))

landsat_9 = ee.ImageCollection("LANDSAT/LC09/C02/T1_TOA")\
    .filterDate(start_date, end_date)\
    .select(['B10', 'B11'])\
    .filter(ee.Filter.lt('CLOUD_COVER', 5))

# ALOS DSM
alos_dsm = ee.Image('JAXA/ALOS/AW3D30/V2_2')\
    .select('AVE_DSM')


In [7]:
print(alos_dsm.bandNames().getInfo())

['AVE_DSM']


In [8]:
sentinel_1_image = sentinel_1.first()

# Get image information
image_info = sentinel_1_image.getInfo()

print(image_info)

{'type': 'Image', 'bands': [{'id': 'VV', 'data_type': {'type': 'PixelType', 'precision': 'double'}, 'dimensions': [29232, 24137], 'crs': 'EPSG:32646', 'crs_transform': [10, 0, 272951.9216847598, 0, -10, 5711121.671456001]}, {'id': 'VH', 'data_type': {'type': 'PixelType', 'precision': 'double'}, 'dimensions': [29232, 24137], 'crs': 'EPSG:32646', 'crs_transform': [10, 0, 272951.9216847598, 0, -10, 5711121.671456001]}, {'id': 'angle', 'data_type': {'type': 'PixelType', 'precision': 'float'}, 'dimensions': [21, 11], 'crs': 'EPSG:32646', 'crs_transform': [-12495.746144253993, -4884.976906068856, 562951.4641484994, 2352.0167217189446, -19781.733454353176, 5662878.602247098]}], 'version': 1708813372914779, 'id': 'COPERNICUS/S1_GRD/S1A_IW_GRDH_1SDV_20160101T000434_20160101T000503_009293_00D6BB_A535', 'properties': {'SNAP_Graph_Processing_Framework_GPF_vers': '6.0.4', 'SLC_Processing_facility_org': 'ESA', 'SLC_Processing_facility_country': 'Germany', 'GRD_Post_Processing_facility_org': 'ESA', '

In [32]:
# Load CSV files
file_paths = [
    'E:\\UCDavis\\QE\\ismn\\california_scan_soil_moisture.csv_part1.csv',
    'E:\\UCDavis\\QE\\ismn\\california_scan_soil_moisture.csv_part2.csv',
    'E:\\UCDavis\\QE\\ismn\\california_scan_soil_moisture.csv_part3.csv'
]

# Concatenate the files into one DataFrame
df = pd.concat((pd.read_csv(f) for f in file_paths), ignore_index=True)

In [33]:
import numpy as np
array_agg = lambda tdf: tdf.tolist()
station_sm_datetime_map = df.groupby("station").aggregate({"soil_moisture": array_agg, "datetime": array_agg, "latitude": max, "longitude": max})

In [34]:
station_sm_datetime_map

soil_moisture  \
station                                                             
AshValley       [0.061, 0.06, 0.061, 0.057, 0.059, 0.055, 0.04...   
BodieHills      [0.084, 0.082, 0.08, 0.083, 0.081, 0.081, 0.07...   
Buckhorn        [0.154, 0.148, 0.15, 0.153, 0.146, 0.15, 0.148...   
Charkiln        [0.013, 0.011, 0.008, 0.007, 0.006, 0.003, 0.0...   
CochoraRanch    [0.08, 0.074, 0.076, 0.069, 0.069, 0.065, 0.06...   
DeathValleyJCT  [0.032, 0.027, 0.03, 0.028, 0.029, 0.031, 0.02...   
DeepSprings     [0.066, 0.068, 0.071, 0.07, 0.066, 0.063, 0.06...   
DesertCenter    [0.0, 0.0, 0.0, 0.016, 0.015, 0.013, 0.013, 0....   
DoeRidge        [0.007, 0.005, 0.0, 0.002, 0.01, 0.01, 0.01, 0...   
EagleLake       [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
Essex           [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
FordDryLake     [0.044, 0.044, 0.038, 0.031, 0.028, 0.036, 0.0...   
FrenchGulch     [0.026, 0.026, 0.025, 0.022, 0.02, 0.023, 0.02...   
KyleCanyon      [0.043, 0.039, 0.037, 0.034, 0.041, 0.04, 0.03...   
LovellSummit    [0.054, 0.052, 0.053, 0.051, 0.047, 0.05, 0.04...   
LovelockNnr     [0.078, 0.074, 0.071, 0.069, 0.07, 0.066, 0.06...   
MarbleCreek     [0.024, 0.023, 0.022, 0.022, 0.016, 0.025, 0.0...   
MonoclineRidge  [0.071, 0.065, 0.066, 0.058, 0.063, 0.061, 0.0...   
PineNut         [0.016, 0.016, 0.013, 0.012, 0.009, 0.011, 0.0...   
PorterCanyon    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
SHELDON         [0.133, 0.133, 0.135, 0.128, 0.132, 0.132, 0.1...   
ShadowMtns      [0.045, 0.045, 0.047, 0.045, 0.045, 0.047, 0.0...   
Stubblefield    [0.161, 0.163, 0.163, 0.159, 0.156, 0.15, 0.15...   
TroughSprings   [0.037, 0.034, 0.036, 0.033, 0.033, 0.031, 0.0...   

                                                         datetime  latitude  \
station                                                                       
AshValley       [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  41.05204   
BodieHills      [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  38.26477   
Buckhorn        [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  40.87959   
Charkiln        [2015-06-27 01:00:00, 2015-06-27 03:00:00, 201...  36.36700   
CochoraRanch    [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  35.12000   
DeathValleyJCT  [2015-08-29 09:00:00, 2015-09-02 12:00:00, 201...  36.33000   
DeepSprings     [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  37.37000   
DesertCenter    [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  33.80000   
DoeRidge        [2015-06-27 03:00:00, 2015-06-27 04:00:00, 201...  37.63000   
EagleLake       [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  40.62000   
Essex           [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  34.67000   
FordDryLake     [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  33.65000   
FrenchGulch     [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  40.79361   
KyleCanyon      [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  36.26700   
LovellSummit    [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  36.16700   
LovelockNnr     [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  40.03300   
MarbleCreek     [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  37.78300   
MonoclineRidge  [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  36.54417   
PineNut         [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  36.56700   
PorterCanyon    [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  39.46700   
SHELDON         [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  41.90000   
ShadowMtns      [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  35.47000   
Stubblefield    [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  34.97018   
TroughSprings   [2015-06-27 01:00:00, 2015-06-27 02:00:00, 201...  36.36700   

                longitude  
station                    
AshValley      -120.68720  
BodieHills     -119.12645  
Buckhorn       -119.95340  
Charkiln       -115.83300  
CochoraRanch   -119.60000  
DeathV

In [35]:
# Extract station coordinates
station_coordinates = station_sm_datetime_map[['latitude', 'longitude']].reset_index()

In [15]:
import datetime as dt

def parse_datetime_and_adjust(image_id):
    if 'S1' in image_id:
        # Sentinel-1 image ID parsing
        parts = image_id.split('_')
        datetime_str = parts[-5]  # The datetime part for Sentinel-1 is the fifth element from the end
        year, month, day = int(datetime_str[:4]), int(datetime_str[4:6]), int(datetime_str[6:8])
        hour, minute, second = int(datetime_str[9:11]), int(datetime_str[11:13]), int(datetime_str[13:15])
        image_datetime = dt.datetime(year, month, day, hour, minute, second)
        # Standardize output by setting minutes and seconds to zero for Sentinel-1
        image_datetime = image_datetime.replace(minute=0, second=0)
    else:
        # For Sentinel-2, extract the datetime part and return it as is
        parts = image_id.split('_')
        datetime_str = parts[2]  # The datetime part for Sentinel-2 is the third element
        year, month, day = int(datetime_str[:4]), int(datetime_str[4:6]), int(datetime_str[6:8])
        time = datetime_str[9:]
        hour, minute, second = int(time[:2]), int(time[2:4]), int(time[4:])
        image_datetime = dt.datetime(year, month, day, hour, minute, second)

    return image_datetime

# Example usage
image_id_s1 = 'COPERNICUS/S1_GRD/S1A_IW_GRDH_1SDV_20160101T000434_20160101T000503_009293_00D6BB_A535'
image_id_s2 = 'COPERNICUS/S2_HARMONIZED/20180729T184919_20180729T185102_T10TFL'

# For Sentinel-1
print("Sentinel-1:", parse_datetime_and_adjust(image_id_s1))
# For Sentinel-2
print("Sentinel-2:", parse_datetime_and_adjust(image_id_s2))


Sentinel-1: 2016-01-01 00:00:00
Sentinel-2: 2018-07-29 18:51:02


In [ ]:
import tqdm

def filter_images_for_station(row):
    station_name = row['station']
    latitude = row['latitude']
    longitude = row['longitude']

    # Define a point geometry for the station
    point = ee.Geometry.Point([longitude, latitude])

    # Filter Sentinel-1 images for this station's point
    sentinel_1_filtered = sentinel_1.filterBounds(point)

    results = []
    # Define the bands to extract from Sentinel-1
    s1_bands = ['VV', 'VH', 'angle']

    for image_info in tqdm.tqdm(sentinel_1_filtered.getInfo()['features']):
        try:
            image_id = image_info['id']
            image = ee.Image(image_id)

            # Extract band values at the station's point
            sample_feature = image.select(s1_bands).sample(point, 10).first()

            if sample_feature:  # Check if the feature is not empty
                band_values = sample_feature.toDictionary().getInfo()
                adjusted_datetime = parse_datetime_and_adjust(image_id)
                results.append((image_id, adjusted_datetime, band_values))
        except ee.EEException as e:
            continue

    return results

# Apply the function to each station and collect results
results_by_station = {}
for index, row in station_coordinates.iterrows():
    station_results = filter_images_for_station(row)
    results_by_station[row['station']] = station_results

# Display the results
for station, results in results_by_station.items():
    print(f"Station: {station}")
    for image_id, datetime, band_values in results:
        print(f"Image ID: {image_id}, Adjusted DateTime: {datetime}")
        print(f"Band values: {band_values}")
    print()  # Add a blank line for better readability




In [163]:
for station, image_data in results_by_station.items():
    if image_data:  # Check if there is any image data
        print(f"Sample data for station {station}: {image_data[0]}")

Sample data for station AshValley: ('COPERNICUS/S1_GRD/S1A_IW_GRDH_1SDV_20160314T015958_20160314T020023_010359_00F590_7575', datetime.datetime(2016, 3, 14, 1, 0), {'VH': -15.849467212748463, 'VV': -13.541761258745398, 'angle': 40.444339752197266})
Sample data for station BodieHills: ('COPERNICUS/S1_GRD/S1A_IW_GRDH_1SDV_20160114T015900_20160114T015925_009484_00DC2E_0BE3', datetime.datetime(2016, 1, 14, 1, 0), {'VH': -17.477792728968847, 'VV': -12.041204486036046, 'angle': 45.05978012084961})
Sample data for station Buckhorn: ('COPERNICUS/S1_GRD/S1A_IW_GRDH_1SDV_20160309T015135_20160309T015200_010286_00F36F_E322', datetime.datetime(2016, 3, 9, 1, 0), {'VH': -19.671675712453215, 'VV': -12.188107439833175, 'angle': 33.55308532714844})
Sample data for station Charkiln: ('COPERNICUS/S1_GRD/S1A_IW_GRDH_1SDV_20160316T014200_20160316T014224_010388_00F643_7B10', datetime.datetime(2016, 3, 16, 1, 0), {'VH': -16.390405584144364, 'VV': -12.541033259138779, 'angle': 39.26993942260742})
Sample data f

In [166]:
# Continue with the filtering process
filtered_station_data = pd.DataFrame(columns=['station', 'soil_moisture', 'datetime', 'latitude', 'longitude'])

# Normalize the datetime in station_sm_datetime_map to the nearest hour
station_sm_datetime_map['datetime'] = station_sm_datetime_map['datetime'].apply(
    lambda dt_list: [pd.to_datetime(dt).replace(minute=0, second=0) for dt in dt_list]
)

# Recheck for common datetimes using results_by_station directly
for station, results in results_by_station.items():
    sentinel_datetimes = set([result[1] for result in results])
    station_data = station_sm_datetime_map.loc[station]
    common_datetimes = sentinel_datetimes.intersection(set(station_data['datetime']))
    if common_datetimes:
        print(f"Common datetimes for {station}: {common_datetimes}")
    else:
        print(f"No common datetimes for {station}")

Common datetimes for AshValley: {datetime.datetime(2022, 6, 11, 2, 0), datetime.datetime(2022, 8, 15, 14, 0), datetime.datetime(2021, 10, 26, 2, 0), datetime.datetime(2021, 8, 3, 2, 0), datetime.datetime(2017, 8, 18, 1, 0), datetime.datetime(2021, 4, 29, 2, 0), datetime.datetime(2021, 10, 7, 14, 0), datetime.datetime(2023, 5, 18, 14, 0), datetime.datetime(2022, 6, 23, 2, 0), datetime.datetime(2022, 10, 14, 14, 0), datetime.datetime(2023, 3, 31, 14, 0), datetime.datetime(2021, 3, 12, 2, 0), datetime.datetime(2021, 5, 16, 14, 0), datetime.datetime(2021, 5, 11, 2, 0), datetime.datetime(2021, 3, 5, 14, 0), datetime.datetime(2023, 8, 5, 2, 0), datetime.datetime(2021, 9, 25, 14, 0), datetime.datetime(2022, 3, 7, 2, 0), datetime.datetime(2022, 3, 19, 2, 0), datetime.datetime(2017, 7, 1, 1, 0), datetime.datetime(2023, 6, 6, 2, 0), datetime.datetime(2023, 1, 13, 2, 0), datetime.datetime(2023, 4, 19, 2, 0), datetime.datetime(2022, 9, 20, 14, 0), datetime.datetime(2023, 8, 17, 2, 0), datetime.dat

In [188]:
# Function to find matching Sentinel-1 data for a given datetime
def find_matching_satellite_data(station_datetime, satellite_data):
    for image_data in satellite_data:
        if image_data[1] == station_datetime:
            return image_data[2]  # Returns only band values since NDVI is not applicable for Sentinel-1
    return None

# Prepare the final dataset
s1_data = []

# Iterate over each station in the station data
for station, station_data in station_sm_datetime_map.iterrows():
    # Get the corresponding Sentinel-1 data for this station
    satellite_data = results_by_station[station]

    for sm, dt in zip(station_data['soil_moisture'], station_data['datetime']):
        # Find matching Sentinel-1 data
        band_values = find_matching_satellite_data(dt, satellite_data)

        if band_values:
            # Append combined data to the final dataset
            s1_data.append({
                'station': station,
                'datetime': dt,
                'soil_moisture': sm,
                'latitude': station_data['latitude'],
                'longitude': station_data['longitude'],
                'VV': band_values.get('VV', None),
                'VH': band_values.get('VH', None),
                'angle': band_values.get('angle', None)
            })

# Convert the final data to a DataFrame
s1_df = pd.DataFrame(s1_data)

# Display the final DataFrame
print(s1_df)

            station            datetime  soil_moisture  latitude  longitude  \
0         AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1         AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2         AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3         AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4         AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   
...             ...                 ...            ...       ...        ...   
8179  TroughSprings 2021-04-25 13:00:00          0.072  36.36700  -115.8000   
8180  TroughSprings 2021-05-01 13:00:00          0.081  36.36700  -115.8000   
8181  TroughSprings 2021-05-07 01:00:00          0.071  36.36700  -115.8000   
8182  TroughSprings 2021-05-07 13:00:00          0.062  36.36700  -115.8000   
8183  TroughSprings 2021-05-13 13:00:00          0.044  36.36700  -115.8000   

             VV         VH      angle  
0    -13.54

In [17]:
# Function to filter Sentinel-2 images based on a station's coordinates and return image band values, NDVI, NDMI, id, and datetime
def filter_sentinel_2_for_station(station_name, latitude, longitude):
    # Define a point geometry
    point = ee.Geometry.Point([longitude, latitude])

    # Filter Sentinel-2 images for this point
    sentinel_2_filtered = sentinel_2.filterBounds(point)
    scaling_factor = 0.0001

    s2_data = []
    for image_info in tqdm.tqdm(sentinel_2_filtered.getInfo()['features']):
        try:
            image_id = image_info['id']
            image = ee.Image(image_id)

            # Calculate NDVI
            ndvi = image.normalizedDifference(['B8', 'B4']).rename('NDVI')
            ndvi_value = ndvi.sample(point, 10).first().get('NDVI').getInfo()

            # Calculate NDMI
            ndmi = image.normalizedDifference(['B8', 'B11']).rename('NDMI')
            ndmi_value = ndmi.sample(point, 10).first().get('NDMI').getInfo()

            # Select the spectral bands for Sentinel-2
            scaled_image = image.select(['B1', 'B2', 'B3', 'B4', 'B5', 'B6', 'B7', 'B8', 'B8A', 'B9', 'B10', 'B11', 'B12']).multiply(scaling_factor)
            band_values = scaled_image.sample(point, 10).first().toDictionary().getInfo()

            adjusted_datetime = parse_datetime_and_adjust(image_id)

            s2_data.append((image_id, adjusted_datetime, band_values, ndvi_value, ndmi_value))
        except ee.EEException as e:
            continue

    return s2_data

# Apply the function to each station and collect results
s2_data_by_station = {}
for station, row in station_sm_datetime_map.iterrows():
    latitude = row['latitude']
    longitude = row['longitude']
    s2_data_by_station[station] = filter_sentinel_2_for_station(station, latitude, longitude)

# Print the results for verification
for station, s2_data in s2_data_by_station.items():
    print(f"Station: {station}")
    for image_id, adjusted_datetime, band_values, ndvi_value, ndmi_value in s2_data:
        print(f"Image ID: {image_id}, datetime:{adjusted_datetime}, NDVI: {ndvi_value}, NDMI: {ndmi_value}")
        print(f"Band values: {band_values}")
    print()  # Add a blank line for better readability


100%|██████████| 940/940 [05:47<00:00,  2.71it/s]

Station: AshValley
Image ID: COPERNICUS/S2_HARMONIZED/20160624T184922_20160624T190210_T10TFL, datetime:2016-06-24 19:02:10, NDVI: 0.13513512909412384, NDMI: -0.10052909702062607
Band values: {'B1': 0.12150000000000001, 'B10': 0.0038, 'B11': 0.2184, 'B12': 0.1875, 'B2': 0.108, 'B3': 0.1095, 'B4': 0.136, 'B5': 0.1545, 'B6': 0.1701, 'B7': 0.1837, 'B8': 0.17850000000000002, 'B8A': 0.19360000000000002, 'B9': 0.11760000000000001}
Image ID: COPERNICUS/S2_HARMONIZED/20160624T190210_20160624T234946_T10TFL, datetime:2016-06-24 23:49:46, NDVI: 0.13513512909412384, NDMI: -0.10052909702062607
Band values: {'B1': 0.12150000000000001, 'B10': 0.0038, 'B11': 0.2184, 'B12': 0.1875, 'B2': 0.108, 'B3': 0.1095, 'B4': 0.136, 'B5': 0.1545, 'B6': 0.1701, 'B7': 0.1837, 'B8': 0.17850000000000002, 'B8A': 0.19360000000000002, 'B9': 0.11760000000000001}
Image ID: COPERNICUS/S2_HARMONIZED/20160714T184922_20160714T190130_T10TFL, datetime:2016-07-14 19:01:30, NDVI: 0.11672908812761307, NDMI: -0.11654321104288101
Band

In [18]:
print(s2_data)

[('COPERNICUS/S2_HARMONIZED/20160206T183306_20160206T215503_T11SNA', datetime.datetime(2016, 2, 6, 21, 55, 3), {'B1': 0.3131, 'B10': 0.0026000000000000003, 'B11': 0.0758, 'B12': 0.0574, 'B2': 0.3141, 'B3': 0.2959, 'B4': 0.3181, 'B5': 0.3491, 'B6': 0.3801, 'B7': 0.38530000000000003, 'B8': 0.3279, 'B8A': 0.3689, 'B9': 0.1704}, 0.015170278958976269, 0.6244736313819885), ('COPERNICUS/S2_HARMONIZED/20160206T183306_20160206T215503_T11SPA', datetime.datetime(2016, 2, 6, 21, 55, 3), {'B1': 0.3128, 'B10': 0.0026000000000000003, 'B11': 0.0758, 'B12': 0.0574, 'B2': 0.3141, 'B3': 0.2959, 'B4': 0.3181, 'B5': 0.3491, 'B6': 0.3801, 'B7': 0.38520000000000004, 'B8': 0.3279, 'B8A': 0.3689, 'B9': 0.1704}, 0.015170278958976269, 0.6244736313819885), ('COPERNICUS/S2_HARMONIZED/20160206T183312_20160206T183306_T11SNA', datetime.datetime(2016, 2, 6, 18, 33, 6), {'B1': 0.3131, 'B10': 0.0026000000000000003, 'B11': 0.0758, 'B12': 0.0574, 'B2': 0.3141, 'B3': 0.2959, 'B4': 0.3181, 'B5': 0.3491, 'B6': 0.3801, 'B7': 

In [19]:
# Load the pickle file
s1_df = pd.read_pickle("E:/UCDavis/AIL/sm/s1_df.pkl")

# Display the first few rows of the DataFrame
s1_df.head()

station            datetime  soil_moisture  latitude  longitude  \
0  AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1  AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2  AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3  AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4  AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   

          VV         VH      angle  
0 -13.541761 -15.849467  40.444340  
1 -11.747905 -18.342907  40.437130  
2 -11.760601 -18.074283  40.442757  
3  -8.847617 -17.027178  40.392700  
4 -13.098324 -19.788079  40.383392

In [28]:
# Create a new DataFrame to store combined Sentinel-1 and Sentinel-2 data
s1_s2_df = s1_df.copy()
s1_s2_df['NDVI'] = None
s1_s2_df['NDMI'] = None

def find_closest_s2_data(station_datetime, s2_data):
    min_diff = pd.Timedelta.max
    closest_data = None
    closest_datetime = None

    for s2_entry in s2_data:
        # Extract datetime from the Sentinel-2 entry
        s2_datetime = s2_entry[1]  # The datetime is the second element in the tuple

        # Calculate the time difference
        time_diff = abs(pd.to_datetime(s2_datetime) - pd.to_datetime(station_datetime))

        # Update if this is the closest data so far
        if time_diff < min_diff:
            min_diff = time_diff
            closest_data = s2_entry[2:]  # Skip the datetime and image_id in the entry
            closest_datetime = s2_datetime

    return closest_data, closest_datetime

# Ensure s1_s2_df has a column for the closest Sentinel-2 datetime
s1_s2_df['s2_closest_datetime'] = None

# Iterate over each row in s1_s2_df
for index, row in s1_s2_df.iterrows():
    station = row['station']
    station_datetime = row['datetime']

    # Get Sentinel-2 data for this station
    s2_data_for_station = s2_data_by_station.get(station, [])

    # Find the closest Sentinel-2 data
    closest_s2_data, closest_s2_datetime = find_closest_s2_data(station_datetime, s2_data_for_station)

    if closest_s2_data:
        # Unpack the data
        band_values, ndvi, ndmi = closest_s2_data

        # Verify that band_values is a dictionary
        if isinstance(band_values, dict):
            # Add each band value to the DataFrame
            for band, value in band_values.items():
                s1_s2_df.at[index, band] = value

        # Add NDVI, NDMI, and the closest Sentinel-2 datetime to the DataFrame
        s1_s2_df.at[index, 'NDVI'] = ndvi
        s1_s2_df.at[index, 'NDMI'] = ndmi
        s1_s2_df.at[index, 's2_closest_datetime'] = closest_s2_datetime

# Display the updated s1_s2_df
print(s1_s2_df)

            station            datetime  soil_moisture  latitude  longitude  \
0         AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1         AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2         AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3         AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4         AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   
...             ...                 ...            ...       ...        ...   
8179  TroughSprings 2021-04-25 13:00:00          0.072  36.36700  -115.8000   
8180  TroughSprings 2021-05-01 13:00:00          0.081  36.36700  -115.8000   
8181  TroughSprings 2021-05-07 01:00:00          0.071  36.36700  -115.8000   
8182  TroughSprings 2021-05-07 13:00:00          0.062  36.36700  -115.8000   
8183  TroughSprings 2021-05-13 13:00:00          0.044  36.36700  -115.8000   

             VV         VH      angle      B1     B

In [30]:
# Saving the s1_s2_df DataFrame to a .pkl file at the specified location
file_path = 'E:/UCDavis/AIL/sm/s1_s2_df.pkl'

# Save the DataFrame
s1_s2_df.to_pickle(file_path)

In [31]:
s1_s2_df = pd.read_pickle(file_path)

s1_s2_df.head()

station            datetime  soil_moisture  latitude  longitude  \
0  AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1  AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2  AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3  AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4  AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   

          VV         VH      angle      B1     B10  ...      B4      B5  \
0 -13.541761 -15.849467  40.444340  0.1215  0.0038  ...  0.1360  0.1545   
1 -11.747905 -18.342907  40.437130  0.1250  0.0019  ...  0.1422  0.1597   
2 -11.760601 -18.074283  40.442757  0.1208  0.0014  ...  0.1049  0.1179   
3  -8.847617 -17.027178  40.392700  0.1151  0.0028  ...  0.0884  0.1017   
4 -13.098324 -19.788079  40.383392  0.1151  0.0028  ...  0.0884  0.1017   

       B6      B7      B8     B8A      B9      NDVI      NDMI  \
0  0.1701  0.1837  0.1785  0.1936  0.1176  0.135135 -0.100529   
1  0.1722  0.1818  0.1721  0.1926  0.0965  0.095132 -0.124173   
2  0.1256  0.1331  0.1294  0.1419  0.0777  0.104567 -0.116724   
3  0.1150  0.1230  0.1200  0.1292  0.0810  0.151631 -0.078341   
4  0.1150  0.1230  0.1200  0.1292  0.0810  0.151631 -0.078341   

   s2_closest_datetime  
0  2016-06-24 19:02:10  
1  2016-08-23 23:55:21  
2  2016-10-22 22:26:47  
3  2017-03-31 18:58:50  
4  2017-03-31 18:58:50  

[5 rows x 24 columns]

In [74]:
import datetime as dt
import tqdm

# Function to parse Landsat datetime from image ID
def parse_landsat_datetime(image_id):
    # Split the image ID by underscore
    parts = image_id.split('_')
    
    # Identify the part that contains the date information
    for part in parts:
        if len(part) == 8 and part.isdigit():
            # This part should be the date part
            year, month, day = int(part[:4]), int(part[4:6]), int(part[6:8])
            return dt.datetime(year, month, day)
    
    # If no date part is found, raise an error
    raise ValueError("Unable to parse Landsat datetime from image ID: " + image_id)

# Function to filter Landsat images based on a station's coordinates and return image band values and datetime
def filter_landsat_for_station(station_name, latitude, longitude):
    # Define a point geometry
    point = ee.Geometry.Point([longitude, latitude])

    # Define combined Landsat image collection
    combined_landsat = landsat_8.merge(landsat_9)

    landsat_filtered = combined_landsat.filterBounds(point)
    landsat_data = []

    for image_info in tqdm.tqdm(landsat_filtered.getInfo()['features']):
        try:
            image_id = image_info['id']
            image = ee.Image(image_id)
            thermal_values = image.select(['B10', 'B11']).sample(point, 30).first().toDictionary().getInfo()
            landsat_datetime = parse_landsat_datetime(image_id)
            landsat_data.append((image_id, landsat_datetime, thermal_values))
        except ee.EEException as e:
            # print(f"Error processing Landsat image {image_id} for station {station_name}: {e}")
            continue

    return landsat_data

# Apply the function to each station and collect results
landsat_data_by_station = {}
for station, row in station_sm_datetime_map.iterrows():
    latitude = row['latitude']
    longitude = row['longitude']
    landsat_data_by_station[station] = filter_landsat_for_station(station, latitude, longitude)

# Print the results for verification
for station, landsat_data in landsat_data_by_station.items():
    print(f"Station: {station}")
    for image_id, landsat_datetime, thermal_values in landsat_data:
        print(f"Image ID: {image_id}, datetime: {landsat_datetime}")
        print(f"Band values: {thermal_values}")


100%|██████████| 205/205 [00:32<00:00,  6.33it/s]

Station: AshValley
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160408, datetime: 2016-04-08 00:00:00
Band values: {'B10': 297.560302734375, 'B11': 296.5682067871094}
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160510, datetime: 2016-05-10 00:00:00
Band values: {'B10': 299.7080078125, 'B11': 299.3487548828125}
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160611, datetime: 2016-06-11 00:00:00
Band values: {'B10': 310.15521240234375, 'B11': 308.9841003417969}
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160627, datetime: 2016-06-27 00:00:00
Band values: {'B10': 318.9933776855469, 'B11': 317.0946044921875}
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160713, datetime: 2016-07-13 00:00:00
Band values: {'B10': 317.87811279296875, 'B11': 316.3886413574219}
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160729, datetime: 2016-07-29 00:00:00
Band values: {'B10': 319.2803955078125, 'B11': 315.72412109375}
Image ID: LANDSAT/LC08/C02/T1_TOA/LC08_044031_20160915, datetime: 2016-09

In [75]:
print(landsat_data)

[('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20171017', datetime.datetime(2017, 10, 17, 0, 0), {'B10': 291.9546203613281, 'B11': 291.35406494140625}), ('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20180427', datetime.datetime(2018, 4, 27, 0, 0), {'B10': 304.3058776855469, 'B11': 303.46636962890625}), ('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20180529', datetime.datetime(2018, 5, 29, 0, 0), {'B10': 288.56854248046875, 'B11': 290.8071594238281}), ('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20200502', datetime.datetime(2020, 5, 2, 0, 0), {'B10': 303.82769775390625, 'B11': 303.254150390625}), ('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20210419', datetime.datetime(2021, 4, 19, 0, 0), {'B10': 302.2186279296875, 'B11': 302.00408935546875}), ('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20210505', datetime.datetime(2021, 5, 5, 0, 0), {'B10': 306.71624755859375, 'B11': 305.9730224609375}), ('LANDSAT/LC08/C02/T1_TOA/LC08_039035_20220321', datetime.datetime(2022, 3, 21, 0, 0), {'B10': 285.8785400390625, 'B11': 285.7545166015625}), (

In [84]:
s1_s2_landsat_df = s1_s2_df.copy()

def find_closest_landsat_data(station_datetime, landsat_data):
    min_diff = pd.Timedelta.max
    closest_data = None
    closest_datetime = None

    for landsat_entry in landsat_data:
        # Extract datetime and band values from the Landsat entry
        image_id, landsat_datetime, thermal_values = landsat_entry

        # Calculate the time difference
        time_diff = abs(landsat_datetime - station_datetime)

        # Update if this is the closest data so far
        if time_diff < min_diff:
            min_diff = time_diff
            closest_data = thermal_values
            closest_datetime = landsat_datetime

    return closest_data, closest_datetime

# Update s1_s2_landsat_df with the closest Landsat data
for index, row in s1_s2_landsat_df.iterrows():
    station = row['station']
    station_datetime = row['datetime']

    # Get Landsat data for this station
    landsat_data_for_station = landsat_data_by_station.get(station, [])

    # Find the closest Landsat data
    closest_thermal_values, closest_landsat_datetime = find_closest_landsat_data(station_datetime, landsat_data_for_station)

    if closest_thermal_values:
        # Update the DataFrame with the closest Landsat data
        s1_s2_landsat_df.at[index, 'landsat_B10'] = closest_thermal_values.get('B10') * 0.0001
        s1_s2_landsat_df.at[index, 'landsat_B11'] = closest_thermal_values.get('B11') * 0.0001
        s1_s2_landsat_df.at[index, 'landsat_closest_datetime'] = closest_landsat_datetime

# Display the updated DataFrame
s1_s2_landsat_df.head()

station            datetime  soil_moisture  latitude  longitude  \
0  AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1  AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2  AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3  AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4  AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   

          VV         VH      angle      B1     B10  ...      B7      B8  \
0 -13.541761 -15.849467  40.444340  0.1215  0.0038  ...  0.1837  0.1785   
1 -11.747905 -18.342907  40.437130  0.1250  0.0019  ...  0.1818  0.1721   
2 -11.760601 -18.074283  40.442757  0.1208  0.0014  ...  0.1331  0.1294   
3  -8.847617 -17.027178  40.392700  0.1151  0.0028  ...  0.1230  0.1200   
4 -13.098324 -19.788079  40.383392  0.1151  0.0028  ...  0.1230  0.1200   

      B8A      B9      NDVI      NDMI  s2_closest_datetime  landsat_B10  \
0  0.1936  0.1176  0.135135 -0.100529  2016-06-24 19:02:10     0.027770   
1  0.1926  0.0965  0.095132 -0.124173  2016-08-23 23:55:21     0.030960   
2  0.1419  0.0777  0.104567 -0.116724  2016-10-22 22:26:47     0.029709   
3  0.1292  0.0810  0.151631 -0.078341  2017-03-31 18:58:50     0.030610   
4  0.1292  0.0810  0.151631 -0.078341  2017-03-31 18:58:50     0.030610   

   landsat_B11  landsat_closest_datetime  
0     0.027756                2016-02-20  
1     0.030783                2016-08-30  
2     0.029675                2016-10-01  
3     0.030399                2017-06-14  
4     0.030399                2017-06-14  

[5 rows x 27 columns]

In [85]:
# Saving the s1_s2_df DataFrame to a .pkl file at the specified location
file_path = 'E:/UCDavis/AIL/sm/scan_s1_s2_landsat_df.pkl'

# Save the DataFrame
s1_s2_landsat_df.to_pickle(file_path)

In [8]:
scan_s1_s2_landsat_df = pd.read_pickle('E:/UCDavis/AIL/sm/scan_s1_s2_landsat_df.pkl')

print(scan_s1_s2_landsat_df)

            station            datetime  soil_moisture  latitude  longitude  \
0         AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1         AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2         AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3         AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4         AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   
...             ...                 ...            ...       ...        ...   
8179  TroughSprings 2021-04-25 13:00:00          0.072  36.36700  -115.8000   
8180  TroughSprings 2021-05-01 13:00:00          0.081  36.36700  -115.8000   
8181  TroughSprings 2021-05-07 01:00:00          0.071  36.36700  -115.8000   
8182  TroughSprings 2021-05-07 13:00:00          0.062  36.36700  -115.8000   
8183  TroughSprings 2021-05-13 13:00:00          0.044  36.36700  -115.8000   

             VV         VH      angle      B1     B

In [7]:
uscrn_s1_s2_landsat_df = pd.read_pickle('E:/UCDavis/AIL/sm/uscrn_s1_s2_landsat_df.pkl')

print(uscrn_s1_s2_landsat_df)

           station            datetime  soil_moisture  latitude  longitude  \
0        Baker-5-W 2016-04-04 01:00:00          0.103   39.0118  -114.2090   
1        Baker-5-W 2016-08-02 01:00:00          0.011   39.0118  -114.2090   
2        Baker-5-W 2016-10-31 01:00:00          0.039   39.0118  -114.2090   
3        Baker-5-W 2016-11-24 01:00:00          0.055   39.0118  -114.2090   
4        Baker-5-W 2017-04-16 13:00:00          0.072   39.0118  -114.2090   
...            ...                 ...            ...       ...        ...   
11469  Yuma-27-ENE 2023-11-30 13:00:00          0.022   32.8350  -114.1884   
11470  Yuma-27-ENE 2023-12-12 01:00:00          0.038   32.8350  -114.1884   
11471  Yuma-27-ENE 2023-12-12 13:00:00          0.037   32.8350  -114.1884   
11472  Yuma-27-ENE 2023-12-24 01:00:00          0.036   32.8350  -114.1884   
11473  Yuma-27-ENE 2023-12-24 13:00:00          0.055   32.8350  -114.1884   

              VV         VH      angle      NDVI      NDMI  ...

In [9]:
uscrn_s1_s2_landsat_df

station            datetime  soil_moisture  latitude  longitude  \
0        Baker-5-W 2016-04-04 01:00:00          0.103   39.0118  -114.2090   
1        Baker-5-W 2016-08-02 01:00:00          0.011   39.0118  -114.2090   
2        Baker-5-W 2016-10-31 01:00:00          0.039   39.0118  -114.2090   
3        Baker-5-W 2016-11-24 01:00:00          0.055   39.0118  -114.2090   
4        Baker-5-W 2017-04-16 13:00:00          0.072   39.0118  -114.2090   
...            ...                 ...            ...       ...        ...   
11469  Yuma-27-ENE 2023-11-30 13:00:00          0.022   32.8350  -114.1884   
11470  Yuma-27-ENE 2023-12-12 01:00:00          0.038   32.8350  -114.1884   
11471  Yuma-27-ENE 2023-12-12 13:00:00          0.037   32.8350  -114.1884   
11472  Yuma-27-ENE 2023-12-24 01:00:00          0.036   32.8350  -114.1884   
11473  Yuma-27-ENE 2023-12-24 13:00:00          0.055   32.8350  -114.1884   

              VV         VH      angle      NDVI      NDMI  ...      B4  \
0     -14.818910 -19.391581  39.805187  0.130324 -0.102471  ...  0.1705   
1     -15.462555 -18.140784  39.801170   0.10989 -0.107347  ...  0.1944   
2     -10.545134 -18.375651  39.831314  0.138346 -0.033621  ...  0.1610   
3     -14.555920 -24.551667  39.832634  0.138346 -0.033621  ...  0.1610   
4     -11.523571 -22.544515  36.442642  0.135294 -0.084404  ...  0.1764   
...          ...        ...        ...       ...       ...  ...     ...   
11469 -14.811567 -28.432496  40.361477  0.040822 -0.207643  ...  0.1586   
11470 -18.025161 -23.553899  32.158283  0.069583 -0.186082  ...  0.1638   
11471 -15.270573 -23.833902  40.351299  0.069583 -0.186082  ...  0.1638   
11472 -12.483473 -21.969465  32.149357  0.056376 -0.210277  ...  0.1565   
11473 -13.371365 -23.588085  40.360901  0.056376 -0.210277  ...  0.1565   

           B5      B6      B7      B8     B8A      B9  landsat_B10  \
0      0.1874  0.2137  0.2328  0.2216  0.2448  0.1249     0.029447   
1      0.2142  0.2387  0.2561  0.2424  0.2728  0.1273     0.031872   
2      0.1662  0.1961  0.2027  0.2127  0.2227  0.1273     0.029385   
3      0.1662  0.1961  0.2027  0.2127  0.2227  0.1273     0.029385   
4      0.1982  0.2298  0.2430  0.2316  0.2568  0.1390     0.030426   
...       ...     ...     ...     ...     ...     ...          ...   
11469  0.1581  0.1749  0.1813  0.1721  0.1938  0.0513     0.029945   
11470  0.1755  0.1922  0.1979  0.1883  0.2110  0.0975     0.029438   
11471  0.1755  0.1922  0.1979  0.1883  0.2110  0.0975     0.029438   
11472  0.1674  0.1766  0.1837  0.1752  0.1979  0.0747     0.029053   
11473  0.1674  0.1766  0.1837  0.1752  0.1979  0.0747     0.029053   

       landsat_B11  landsat_closest_datetime  
0         0.029385                2016-04-05  
1         0.031693                2016-07-26  
2         0.029368                2016-11-15  
3         0.029368                2016-11-15  
4         0.030323                2017-05-10  
...            ...                       ...  
11469     0.029950                2023-12-06  
11470     0.029475                2023-12-14  
11471     0.029475                2023-12-14  
11472     0.029109                2023-12-30  
11473     0.029109                2023-12-30  

[11474 rows x 27 columns]

In [10]:
merged_df = pd.concat([scan_s1_s2_landsat_df, uscrn_s1_s2_landsat_df], ignore_index=True)

In [11]:
merged_df

station            datetime  soil_moisture  latitude  longitude  \
0        AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1        AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2        AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3        AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4        AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   
...            ...                 ...            ...       ...        ...   
19653  Yuma-27-ENE 2023-11-30 13:00:00          0.022  32.83500  -114.1884   
19654  Yuma-27-ENE 2023-12-12 01:00:00          0.038  32.83500  -114.1884   
19655  Yuma-27-ENE 2023-12-12 13:00:00          0.037  32.83500  -114.1884   
19656  Yuma-27-ENE 2023-12-24 01:00:00          0.036  32.83500  -114.1884   
19657  Yuma-27-ENE 2023-12-24 13:00:00          0.055  32.83500  -114.1884   

              VV         VH      angle      B1     B10  ...      B7      B8  \
0     -13.541761 -15.849467  40.444340  0.1215  0.0038  ...  0.1837  0.1785   
1     -11.747905 -18.342907  40.437130  0.1250  0.0019  ...  0.1818  0.1721   
2     -11.760601 -18.074283  40.442757  0.1208  0.0014  ...  0.1331  0.1294   
3      -8.847617 -17.027178  40.392700  0.1151  0.0028  ...  0.1230  0.1200   
4     -13.098324 -19.788079  40.383392  0.1151  0.0028  ...  0.1230  0.1200   
...          ...        ...        ...     ...     ...  ...     ...     ...   
19653 -14.811567 -28.432496  40.361477  0.1614  0.0015  ...  0.1813  0.1721   
19654 -18.025161 -23.553899  32.158283  0.1759  0.0019  ...  0.1979  0.1883   
19655 -15.270573 -23.833902  40.351299  0.1759  0.0019  ...  0.1979  0.1883   
19656 -12.483473 -21.969465  32.149357  0.1732  0.0014  ...  0.1837  0.1752   
19657 -13.371365 -23.588085  40.360901  0.1732  0.0014  ...  0.1837  0.1752   

          B8A      B9      NDVI      NDMI  s2_closest_datetime  landsat_B10  \
0      0.1936  0.1176  0.135135 -0.100529  2016-06-24 19:02:10     0.027770   
1      0.1926  0.0965  0.095132 -0.124173  2016-08-23 23:55:21     0.030960   
2      0.1419  0.0777  0.104567 -0.116724  2016-10-22 22:26:47     0.029709   
3      0.1292  0.0810  0.151631 -0.078341  2017-03-31 18:58:50     0.030610   
4      0.1292  0.0810  0.151631 -0.078341  2017-03-31 18:58:50     0.030610   
...       ...     ...       ...       ...                  ...          ...   
19653  0.1938  0.0513  0.040822 -0.207643  2023-12-01 18:34:36     0.029945   
19654  0.2110  0.0975  0.069583 -0.186082  2023-12-13 18:18:18     0.029438   
19655  0.2110  0.0975  0.069583 -0.186082  2023-12-13 18:18:18     0.029438   
19656  0.1979  0.0747  0.056376 -0.210277  2023-12-28 18:17:51     0.029053   
19657  0.1979  0.0747  0.056376 -0.210277  2023-12-28 18:17:51     0.029053   

       landsat_B11  landsat_closest_datetime  
0         0.027756                2016-02-20  
1         0.030783                2016-08-30  
2         0.029675                2016-10-01  
3         0.030399                2017-06-14  
4         0.030399                2017-06-14  
...            ...                       ...  
19653     0.029950                2023-12-06  
19654     0.029475                2023-12-14  
19655     0.029475                2023-12-14  
19656     0.029109                2023-12-30  
19657     0.029109                2023-12-30  

[19658 rows x 27 columns]

In [ ]:
def filter_smap_for_station(station_name, latitude, longitude):
    # Define a point geometry
    point = ee.Geometry.Point([longitude, latitude])

    # Filter SMAP images for this point
    smap_filtered = smap.filterBounds(point)

    smap_data = []
    for image_info in tqdm.tqdm(smap_filtered.getInfo()['features']):
        try:
            image_id = image_info['id']
            image = ee.Image(image_id)

            # Select the spectral bands for Sentinel-2
            available_bands = ['soil_moisture_am']
            band_values = image.select(available_bands).sample(point, 9000).first().toDictionary().getInfo()

            smap_data.append((image_id, band_values))
        except ee.EEException as e:
            #print(f"Error processing SMAP image {image_id} for station {station_name}: {e}")
            continue

    return smap_data

# Apply the function to each station and collect results
smap_data_by_station = {}
for station, row in station_sm_datetime_map.iterrows():
    latitude = row['latitude']
    longitude = row['longitude']
    smap_data_by_station[station] = filter_smap_for_station(station, latitude, longitude)

# Print the results for verification
for station, smap_data in smap_data_by_station.items():
    print(f"Station: {station}")
    for image_id, band_values in smap_data:
        print(f"Image ID: {image_id}")
        print(f"Band values: {band_values}")
    print()  # Add a blank line for better readability


In [92]:
# Save the DataFrame as a CSV file
csv_file_path = 'E:/UCDavis/AIL/sm/combined_station_satellite_data.csv'
final_df.to_csv(csv_file_path, index=False)

In [12]:
final_df_csv = merged_df

In [13]:
final_df_csv

station            datetime  soil_moisture  latitude  longitude  \
0        AshValley 2016-03-14 01:00:00          0.256  41.05204  -120.6872   
1        AshValley 2016-08-29 02:00:00          0.040  41.05204  -120.6872   
2        AshValley 2016-11-03 01:00:00          0.129  41.05204  -120.6872   
3        AshValley 2017-02-18 14:00:00          0.174  41.05204  -120.6872   
4        AshValley 2017-03-15 01:00:00          0.159  41.05204  -120.6872   
...            ...                 ...            ...       ...        ...   
19653  Yuma-27-ENE 2023-11-30 13:00:00          0.022  32.83500  -114.1884   
19654  Yuma-27-ENE 2023-12-12 01:00:00          0.038  32.83500  -114.1884   
19655  Yuma-27-ENE 2023-12-12 13:00:00          0.037  32.83500  -114.1884   
19656  Yuma-27-ENE 2023-12-24 01:00:00          0.036  32.83500  -114.1884   
19657  Yuma-27-ENE 2023-12-24 13:00:00          0.055  32.83500  -114.1884   

              VV         VH      angle      B1     B10  ...      B7      B8  \
0     -13.541761 -15.849467  40.444340  0.1215  0.0038  ...  0.1837  0.1785   
1     -11.747905 -18.342907  40.437130  0.1250  0.0019  ...  0.1818  0.1721   
2     -11.760601 -18.074283  40.442757  0.1208  0.0014  ...  0.1331  0.1294   
3      -8.847617 -17.027178  40.392700  0.1151  0.0028  ...  0.1230  0.1200   
4     -13.098324 -19.788079  40.383392  0.1151  0.0028  ...  0.1230  0.1200   
...          ...        ...        ...     ...     ...  ...     ...     ...   
19653 -14.811567 -28.432496  40.361477  0.1614  0.0015  ...  0.1813  0.1721   
19654 -18.025161 -23.553899  32.158283  0.1759  0.0019  ...  0.1979  0.1883   
19655 -15.270573 -23.833902  40.351299  0.1759  0.0019  ...  0.1979  0.1883   
19656 -12.483473 -21.969465  32.149357  0.1732  0.0014  ...  0.1837  0.1752   
19657 -13.371365 -23.588085  40.360901  0.1732  0.0014  ...  0.1837  0.1752   

          B8A      B9      NDVI      NDMI  s2_closest_datetime  landsat_B10  \
0      0.1936  0.1176  0.135135 -0.100529  2016-06-24 19:02:10     0.027770   
1      0.1926  0.0965  0.095132 -0.124173  2016-08-23 23:55:21     0.030960   
2      0.1419  0.0777  0.104567 -0.116724  2016-10-22 22:26:47     0.029709   
3      0.1292  0.0810  0.151631 -0.078341  2017-03-31 18:58:50     0.030610   
4      0.1292  0.0810  0.151631 -0.078341  2017-03-31 18:58:50     0.030610   
...       ...     ...       ...       ...                  ...          ...   
19653  0.1938  0.0513  0.040822 -0.207643  2023-12-01 18:34:36     0.029945   
19654  0.2110  0.0975  0.069583 -0.186082  2023-12-13 18:18:18     0.029438   
19655  0.2110  0.0975  0.069583 -0.186082  2023-12-13 18:18:18     0.029438   
19656  0.1979  0.0747  0.056376 -0.210277  2023-12-28 18:17:51     0.029053   
19657  0.1979  0.0747  0.056376 -0.210277  2023-12-28 18:17:51     0.029053   

       landsat_B11  landsat_closest_datetime  
0         0.027756                2016-02-20  
1         0.030783                2016-08-30  
2         0.029675                2016-10-01  
3         0.030399                2017-06-14  
4         0.030399                2017-06-14  
...            ...                       ...  
19653     0.029950                2023-12-06  
19654     0.029475                2023-12-14  
19655     0.029475                2023-12-14  
19656     0.029109                2023-12-30  
19657     0.029109                2023-12-30  

[19658 rows x 27 columns]

In [14]:
import torch
from torch.utils.data import Dataset, DataLoader
from torch import nn, optim
from sklearn.model_selection import train_test_split

# Define a custom dataset class
class CustomDataset(Dataset):
    def __init__(self, features, labels):
        self.features = features
        self.labels = labels

    def __len__(self):
        return len(self.features)

    def __getitem__(self, idx):
        return self.features[idx], self.labels[idx]

# Assuming final_df is the DataFrame and it contains the necessary columns
#feature_columns = ['VV','VH','angle','B1', 'B2', 'B3', 'B4', 'B5', 'B6', 'B7', 'B8', 'B8A', 'B9', 'B10', 'B11', 'B12', 'NDVI','NDMI', 'landsat_B10', 'landsat_B11']
feature_columns = ['VV','VH','NDVI','NDMI']
target_column = 'soil_moisture'


In [15]:
for column in feature_columns:
    final_df_csv[column] = pd.to_numeric(final_df_csv[column], errors='coerce')

# Handle missing values, for example, by filling with 0 or column mean
final_df_csv.fillna(0, inplace=True)  # Or use: final_df_csv.fillna(final_df_csv.mean(), inplace=True)


In [16]:
final_df_csv['soil_moisture'] = final_df_csv['soil_moisture'] * 100
print(final_df_csv)

           station            datetime  soil_moisture  latitude  longitude  \
0        AshValley 2016-03-14 01:00:00           25.6  41.05204  -120.6872   
1        AshValley 2016-08-29 02:00:00            4.0  41.05204  -120.6872   
2        AshValley 2016-11-03 01:00:00           12.9  41.05204  -120.6872   
3        AshValley 2017-02-18 14:00:00           17.4  41.05204  -120.6872   
4        AshValley 2017-03-15 01:00:00           15.9  41.05204  -120.6872   
...            ...                 ...            ...       ...        ...   
19653  Yuma-27-ENE 2023-11-30 13:00:00            2.2  32.83500  -114.1884   
19654  Yuma-27-ENE 2023-12-12 01:00:00            3.8  32.83500  -114.1884   
19655  Yuma-27-ENE 2023-12-12 13:00:00            3.7  32.83500  -114.1884   
19656  Yuma-27-ENE 2023-12-24 01:00:00            3.6  32.83500  -114.1884   
19657  Yuma-27-ENE 2023-12-24 13:00:00            5.5  32.83500  -114.1884   

              VV         VH      angle      B1     B10  ...    

In [17]:
# Split the data into features and target
X = final_df_csv[feature_columns].values
y = final_df_csv[target_column].values

# Splitting the dataset into training, testing, and validation sets
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.2, random_state=42)
X_test, X_val, y_test, y_val = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

# Convert to PyTorch tensors
X_train_tensor = torch.tensor(X_train, dtype=torch.float32)
y_train_tensor = torch.tensor(y_train, dtype=torch.float32)
X_test_tensor = torch.tensor(X_test, dtype=torch.float32)
y_test_tensor = torch.tensor(y_test, dtype=torch.float32)
X_val_tensor = torch.tensor(X_val, dtype=torch.float32)
y_val_tensor = torch.tensor(y_val, dtype=torch.float32)

# Create datasets
train_dataset = CustomDataset(X_train_tensor, y_train_tensor)
test_dataset = CustomDataset(X_test_tensor, y_test_tensor)
val_dataset = CustomDataset(X_val_tensor, y_val_tensor)

# Data loaders
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False)


In [18]:
print(X)

[[-13.54176126 -15.84946721   0.13513513  -0.1005291 ]
 [-11.74790523 -18.34290657   0.09513204  -0.12417303]
 [-11.76060077 -18.07428279   0.1045668   -0.11672355]
 ...
 [-15.27057265 -23.83390151   0.06958251  -0.18608169]
 [-12.48347274 -21.96946459   0.05637624  -0.21027721]
 [-13.37136491 -23.5880848    0.05637624  -0.21027721]]


In [19]:
# Define the transformer model
class TransformerModel(nn.Module):
    def __init__(self, input_size, num_layers, dim_feedforward, dropout=0.1):
        super(TransformerModel, self).__init__()
        # Adjust num_heads to be a factor of input_size
        num_heads = 2 if input_size % 2 == 0 else 1
        self.transformer_layer = nn.TransformerEncoderLayer(
            d_model=input_size,
            nhead=num_heads,
            dim_feedforward=dim_feedforward,
            dropout=dropout
        )
        self.transformer_encoder = nn.TransformerEncoder(self.transformer_layer, num_layers=num_layers)
        self.fc = nn.Linear(input_size, 1)

    def forward(self, src):
        out = self.transformer_encoder(src)
        out = self.fc(out.mean(dim=1))
        return out

# Instantiate the model
input_size = len(feature_columns)
Transformer_model = TransformerModel(input_size=input_size, num_layers=2, dim_feedforward=512)


# Loss and optimizer
criterion = nn.MSELoss()
optimizer = optim.Adam(Transformer_model.parameters(), lr=0.00001)

# Training loop
num_epochs = 50
for epoch in range(num_epochs):
    Transformer_model.train()
    for inputs, targets in train_loader:
        # Reshape inputs for Transformer: (batch_size, seq_len, features)
        inputs = inputs.unsqueeze(1)

        # Forward pass
        outputs = Transformer_model(inputs)
        loss = criterion(outputs, targets)

        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')

# Evaluate the model
Transformer_model.eval()
with torch.no_grad():
    total_loss = 0
    for inputs, targets in test_loader:
        inputs = inputs.unsqueeze(1)
        outputs = Transformer_model(inputs)
        loss = criterion(outputs, targets)
        total_loss += loss.item()

    print(f'Test Loss: {total_loss / len(test_loader):.4f}')

c:\Users\jiyuc\anaconda3\envs\myenv\Lib\site-packages\torch\nn\modules\transformer.py:286: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")
c:\Users\jiyuc\anaconda3\envs\myenv\Lib\site-packages\torch\nn\modules\loss.py:535: UserWarning: Using a target size (torch.Size([32])) that is different to the input size (torch.Size([32, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)
c:\Users\jiyuc\anaconda3\envs\myenv\Lib\site-packages\torch\nn\modules\loss.py:535: UserWarning: Using a target size (torch.Size([14])) that is different to the input size (torch.Size([14, 1])). This will likely lead to incorrect results due

Epoch [1/50], Loss: 107.0225
Epoch [2/50], Loss: 57.3065
Epoch [3/50], Loss: 151.4533
Epoch [4/50], Loss: 61.1937
Epoch [5/50], Loss: 123.5787
Epoch [6/50], Loss: 98.6474
Epoch [7/50], Loss: 116.0326
Epoch [8/50], Loss: 115.1079
Epoch [9/50], Loss: 99.5376
Epoch [10/50], Loss: 269.2975
Epoch [11/50], Loss: 58.3773
Epoch [12/50], Loss: 124.4801
Epoch [13/50], Loss: 68.9536
Epoch [14/50], Loss: 54.3344
Epoch [15/50], Loss: 51.0841
Epoch [16/50], Loss: 59.7923
Epoch [17/50], Loss: 78.2601
Epoch [18/50], Loss: 53.7598
Epoch [19/50], Loss: 138.5379
Epoch [20/50], Loss: 43.8798
Epoch [21/50], Loss: 70.7765
Epoch [22/50], Loss: 163.5049
Epoch [23/50], Loss: 67.9704
Epoch [24/50], Loss: 222.2391
Epoch [25/50], Loss: 153.4806
Epoch [26/50], Loss: 163.2471
Epoch [27/50], Loss: 151.7937
Epoch [28/50], Loss: 101.8671
Epoch [29/50], Loss: 31.6800
Epoch [30/50], Loss: 121.6296
Epoch [31/50], Loss: 125.9016
Epoch [32/50], Loss: 139.2285
Epoch [33/50], Loss: 53.1487
Epoch [34/50], Loss: 228.4093
Epoch

In [151]:
feature_columns

['VV', 'VH', 'NDVI', 'NDMI']

In [20]:
# Define the DNN model
class DNNModel(nn.Module):
    def __init__(self, input_size, hidden_layer_sizes, dropout=0.1):
        super(DNNModel, self).__init__()
        layers = []

        # Add the first layer
        layers.append(nn.Linear(input_size, hidden_layer_sizes[0]))
        layers.append(nn.ReLU())
        layers.append(nn.Dropout(dropout))

        # Add any additional layers

        for i in range(1, len(hidden_layer_sizes)):
            layers.append(nn.Linear(hidden_layer_sizes[i-1], hidden_layer_sizes[i]))
            layers.append(nn.ReLU())
            layers.append(nn.Dropout(dropout))

        # Output layer
        layers.append(nn.Linear(hidden_layer_sizes[-1], 1))

        self.layers = nn.Sequential(*layers)

    def forward(self, x):
        return self.layers(x)

# Instantiate the DNN model
input_size = len(feature_columns)
hidden_layer_sizes = [32, 64, 128, 64, 32]  # Example sizes for hidden layers
dnn_model = DNNModel(input_size=input_size, hidden_layer_sizes=hidden_layer_sizes, dropout=0.1)

# Loss and optimizer for DNN
optimizer = optim.Adam(dnn_model.parameters(), lr=0.01)

num_epochs = 50
# Training loop for DNN
for epoch in range(num_epochs):
    dnn_model.train()
    for inputs, targets in train_loader:
        # Forward pass
        outputs = dnn_model(inputs)
        loss = criterion(outputs, targets)

        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    print(f'DNN - Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')

# Evaluate the DNN model
dnn_model.eval()
with torch.no_grad():
    total_loss = 0
    for inputs, targets in test_loader:
        outputs = dnn_model(inputs)
        loss = criterion(outputs, targets)
        total_loss += loss.item()

    print(f'DNN - Test Loss: {total_loss / len(test_loader):.4f}')

DNN - Epoch [1/50], Loss: 57.4531
DNN - Epoch [2/50], Loss: 99.1432
DNN - Epoch [3/50], Loss: 50.2110
DNN - Epoch [4/50], Loss: 46.3502
DNN - Epoch [5/50], Loss: 50.5265
DNN - Epoch [6/50], Loss: 65.4781
DNN - Epoch [7/50], Loss: 71.0635
DNN - Epoch [8/50], Loss: 62.1523
DNN - Epoch [9/50], Loss: 35.7706
DNN - Epoch [10/50], Loss: 32.3575
DNN - Epoch [11/50], Loss: 56.3955
DNN - Epoch [12/50], Loss: 43.6631
DNN - Epoch [13/50], Loss: 52.9828
DNN - Epoch [14/50], Loss: 84.8947
DNN - Epoch [15/50], Loss: 152.2735
DNN - Epoch [16/50], Loss: 107.4214
DNN - Epoch [17/50], Loss: 30.8705
DNN - Epoch [18/50], Loss: 84.0616
DNN - Epoch [19/50], Loss: 81.4670
DNN - Epoch [20/50], Loss: 34.0162
DNN - Epoch [21/50], Loss: 45.8289
DNN - Epoch [22/50], Loss: 36.9000
DNN - Epoch [23/50], Loss: 30.5472
DNN - Epoch [24/50], Loss: 46.1393
DNN - Epoch [25/50], Loss: 47.6267
DNN - Epoch [26/50], Loss: 83.3740
DNN - Epoch [27/50], Loss: 48.4557
DNN - Epoch [28/50], Loss: 57.1179
DNN - Epoch [29/50], Loss: 

In [23]:
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error

def calculate_mape(y_true, y_pred):
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

# Function to evaluate the model
def evaluate_model(model, loader):
    model.eval()
    predictions = []
    actuals = []
    with torch.no_grad():
        for inputs, targets in loader:
            # Reshape for Transformer
            if isinstance(model, TransformerModel):
                inputs = inputs.unsqueeze(1)

            outputs = model(inputs)
            predictions.extend(outputs.view(-1).tolist())
            actuals.extend(targets.tolist())
    
    predictions = np.array(predictions)
    actuals = np.array(actuals)

    r2 = r2_score(actuals, predictions)
    rmse = np.sqrt(mean_squared_error(actuals, predictions))
    mae = mean_absolute_error(actuals, predictions)
    mape = calculate_mape(actuals, predictions)

    return r2, rmse, mae, mape

# Evaluate Transformer Model
r2_transformer, rmse_transformer, mae_transformer, mape_transformer = evaluate_model(Transformer_model, val_loader)
print(f'Transformer Model - R2: {r2_transformer:.4f}, RMSE: {rmse_transformer:.4f}, MAE: {mae_transformer:.4f}, MAPE: {mape_transformer:.4f}%')

# Evaluate DNN Model
r2_dnn, rmse_dnn, mae_dnn, mape_dnn = evaluate_model(dnn_model, val_loader)
print(f'DNN Model - R2: {r2_dnn:.4f}, RMSE: {rmse_dnn:.4f}, MAE: {mae_dnn:.4f}, MAPE: {mape_dnn:.4f}%')


Transformer Model - R2: -0.4700, RMSE: 10.1865, MAE: 6.9782, MAPE: inf%
DNN Model - R2: -0.0001, RMSE: 8.4022, MAE: 6.6328, MAPE: inf%


C:\Users\jiyuc\AppData\Local\Temp\ipykernel_19136\660288644.py:4: RuntimeWarning: divide by zero encountered in divide
  return np.mean(np.abs((y_true - y_pred) / y_true)) * 100
C:\Users\jiyuc\AppData\Local\Temp\ipykernel_19136\660288644.py:4: RuntimeWarning: divide by zero encountered in divide
  return np.mean(np.abs((y_true - y_pred) / y_true)) * 100


In [33]:
# Define the LSTM model
class LSTMModel(nn.Module):
    def __init__(self, input_size, lstm_hidden_size, num_layers, dropout=0.1):
        super(LSTMModel, self).__init__()
        self.lstm = nn.LSTM(input_size, lstm_hidden_size, num_layers, batch_first=True, dropout=dropout)
        self.fc = nn.Linear(lstm_hidden_size, 1)

    def forward(self, src):
        # LSTM output
        lstm_out, _ = self.lstm(src)
        # Final output - taking the output of the last time step
        out = self.fc(lstm_out[:, -1, :])
        return out

# Instantiate the LSTM model
lstm_hidden_size = 32  # Example value, adjust as needed
num_layers = 2  # Number of LSTM layers
lstm_model = LSTMModel(input_size=input_size, lstm_hidden_size=lstm_hidden_size, num_layers=num_layers, dropout=0.1)

# Loss and optimizer for LSTM
optimizer = optim.Adam(lstm_model.parameters(), lr=0.001)

# Training loop for LSTM
for epoch in range(num_epochs):
    lstm_model.train()
    for inputs, targets in train_loader:
        # Reshape inputs for LSTM: (batch_size, seq_len, features)
        inputs = inputs.unsqueeze(1)

        # Forward pass
        outputs = lstm_model(inputs)
        loss = criterion(outputs, targets)

        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    print(f'LSTM - Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')

# Evaluate the LSTM model
lstm_model.eval()
with torch.no_grad():
    total_loss = 0
    for inputs, targets in test_loader:
        inputs = inputs.unsqueeze(1)
        outputs = lstm_model(inputs)
        loss = criterion(outputs, targets)
        total_loss += loss.item()

    print(f'LSTM - Test Loss: {total_loss / len(test_loader):.4f}')


c:\Users\jiyuc\anaconda3\envs\myenv\Lib\site-packages\torch\nn\modules\loss.py:535: UserWarning: Using a target size (torch.Size([32])) that is different to the input size (torch.Size([32, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)
c:\Users\jiyuc\anaconda3\envs\myenv\Lib\site-packages\torch\nn\modules\loss.py:535: UserWarning: Using a target size (torch.Size([14])) that is different to the input size (torch.Size([14, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


LSTM - Epoch [1/50], Loss: 155.6636
LSTM - Epoch [2/50], Loss: 43.1268
LSTM - Epoch [3/50], Loss: 52.9241
LSTM - Epoch [4/50], Loss: 111.2667
LSTM - Epoch [5/50], Loss: 78.4797
LSTM - Epoch [6/50], Loss: 46.6426
LSTM - Epoch [7/50], Loss: 56.4363
LSTM - Epoch [8/50], Loss: 56.4269
LSTM - Epoch [9/50], Loss: 75.8252
LSTM - Epoch [10/50], Loss: 61.5424
LSTM - Epoch [11/50], Loss: 50.2238
LSTM - Epoch [12/50], Loss: 58.3565
LSTM - Epoch [13/50], Loss: 34.1778
LSTM - Epoch [14/50], Loss: 106.6210
LSTM - Epoch [15/50], Loss: 55.7357
LSTM - Epoch [16/50], Loss: 86.1178
LSTM - Epoch [17/50], Loss: 63.0179
LSTM - Epoch [18/50], Loss: 68.3274
LSTM - Epoch [19/50], Loss: 36.7140
LSTM - Epoch [20/50], Loss: 59.4630
LSTM - Epoch [21/50], Loss: 52.2424
LSTM - Epoch [22/50], Loss: 85.7775
LSTM - Epoch [23/50], Loss: 54.7635
LSTM - Epoch [24/50], Loss: 32.6804
LSTM - Epoch [25/50], Loss: 44.2556
LSTM - Epoch [26/50], Loss: 74.9881
LSTM - Epoch [27/50], Loss: 112.7714
LSTM - Epoch [28/50], Loss: 38.45

In [27]:
# Define the LSTM-Transformer model
class LSTMTransformerModel(nn.Module):
    def __init__(self, input_size, lstm_hidden_size, num_layers, num_heads, dim_feedforward, dropout=0.1):
        super(LSTMTransformerModel, self).__init__()
        self.lstm = nn.LSTM(input_size, lstm_hidden_size, batch_first=True)
        self.transformer_layer = nn.TransformerEncoderLayer(
            d_model=lstm_hidden_size,
            nhead=num_heads,
            dim_feedforward=dim_feedforward,
            dropout=dropout
        )
        self.transformer_encoder = nn.TransformerEncoder(self.transformer_layer, num_layers=num_layers)
        self.fc = nn.Linear(lstm_hidden_size, 1)

    def forward(self, src):
        lstm_out, _ = self.lstm(src)
        transformer_out = self.transformer_encoder(lstm_out)
        out = self.fc(transformer_out.mean(dim=1))
        return out

# Model parameters
input_size = len(feature_columns)
lstm_hidden_size = 32  # Example value, adjust as needed
num_layers = 2
num_heads = 4  # Ensure this is an appropriate divisor of lstm_hidden_size
dim_feedforward = 512
dropout_rate = 0.1  # Dropout rate

# Instantiate the LSTM-Transformer model
lstm_transformer_model = LSTMTransformerModel(input_size, lstm_hidden_size, num_layers, num_heads, dim_feedforward, dropout=0.1)

# Loss and optimizer for LSTM-Transformer
optimizer = optim.Adam(lstm_transformer_model.parameters(), lr=0.001)

# Training loop for LSTM-Transformer
num_epochs = 50
for epoch in range(num_epochs):
    lstm_transformer_model.train()
    for inputs, targets in train_loader:
        inputs = inputs.unsqueeze(1)  # Reshape inputs for LSTM
        outputs = lstm_transformer_model(inputs)
        loss = criterion(outputs, targets)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
    print(f'LSTM-Transformer - Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')

# Evaluate the LSTM-Transformer model
lstm_transformer_model.eval()
with torch.no_grad():
    total_loss = 0
    for inputs, targets in test_loader:
        inputs = inputs.unsqueeze(1)
        outputs = lstm_transformer_model(inputs)
        loss = criterion(outputs, targets)
        total_loss += loss.item()
    print(f'LSTM-Transformer - Test Loss: {total_loss / len(test_loader):.4f}')


LSTM-Transformer - Epoch [1/50], Loss: 127.3611
LSTM-Transformer - Epoch [2/50], Loss: 186.1676
LSTM-Transformer - Epoch [3/50], Loss: 43.2633
LSTM-Transformer - Epoch [4/50], Loss: 48.8799
LSTM-Transformer - Epoch [5/50], Loss: 52.0031
LSTM-Transformer - Epoch [6/50], Loss: 106.2489
LSTM-Transformer - Epoch [7/50], Loss: 36.3152
LSTM-Transformer - Epoch [8/50], Loss: 29.0582
LSTM-Transformer - Epoch [9/50], Loss: 80.5829
LSTM-Transformer - Epoch [10/50], Loss: 59.3054
LSTM-Transformer - Epoch [11/50], Loss: 60.8058
LSTM-Transformer - Epoch [12/50], Loss: 92.7381
LSTM-Transformer - Epoch [13/50], Loss: 37.7201
LSTM-Transformer - Epoch [14/50], Loss: 53.2573
LSTM-Transformer - Epoch [15/50], Loss: 63.0111
LSTM-Transformer - Epoch [16/50], Loss: 52.3990
LSTM-Transformer - Epoch [17/50], Loss: 81.8576
LSTM-Transformer - Epoch [18/50], Loss: 46.1582
LSTM-Transformer - Epoch [19/50], Loss: 35.4611
LSTM-Transformer - Epoch [20/50], Loss: 100.4539
LSTM-Transformer - Epoch [21/50], Loss: 202.1

In [50]:
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error
from scipy.stats import pearsonr

def calculate_mape(y_true, y_pred, epsilon=1e-8):
    y_true = np.array(y_true)
    y_pred = np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / (y_true + epsilon))) * 100

def evaluate_model(model, loader):
    model.eval()
    predictions = []
    actuals = []
    with torch.no_grad():
        for inputs, targets in loader:
            # Reshape for LSTM and Transformer models
            if isinstance(model, (LSTMModel, TransformerModel, LSTMTransformerModel)):
                inputs = inputs.unsqueeze(1)

            outputs = model(inputs)
            predictions.extend(outputs.view(-1).tolist())
            actuals.extend(targets.tolist())

    predictions = np.array(predictions, dtype=np.float32)
    actuals = np.array(actuals, dtype=np.float32)

    mask = ~np.isnan(predictions) & ~np.isnan(actuals)
    predictions = predictions[mask]
    actuals = actuals[mask]

    r2 = r2_score(actuals, predictions)
    rmse = np.sqrt(mean_squared_error(actuals, predictions))
    mae = mean_absolute_error(actuals, predictions)
    mape = calculate_mape(actuals, predictions)

    # Check for constant values
    if np.std(actuals) == 0 or np.std(predictions) == 0:
        pearson_corr = np.nan
    else:
        pearson_corr, _ = pearsonr(actuals, predictions)

    return r2, rmse, mae, mape, pearson_corr


# Evaluate Transformer Model
r2_transformer, rmse_transformer, mae_transformer, mape_transformer, pearson_transformer = evaluate_model(Transformer_model, val_loader)
print(f'Transformer Model - Pearson R: {pearson_transformer:.4f}, R2: {r2_transformer:.4f}, RMSE: {rmse_transformer:.4f}, MAE: {mae_transformer:.4f}, MAPE: {mape_transformer:.4f}%')

# Evaluate DNN Model
r2_dnn, rmse_dnn, mae_dnn, mape_dnn, pearson_dnn = evaluate_model(dnn_model, val_loader)
print(f'DNN Model - Pearson R: {pearson_dnn:.4f}, R2: {r2_dnn:.4f}, RMSE: {rmse_dnn:.4f}, MAE: {mae_dnn:.4f}, MAPE: {mape_dnn:.4f}%')

# Evaluate LSTM Model
r2_lstm, rmse_lstm, mae_lstm, mape_lstm, pearson_lstm = evaluate_model(lstm_model, val_loader)
print(f'LSTM Model - Pearson R: {pearson_lstm:.4f}, R2: {r2_lstm:.4f}, RMSE: {rmse_lstm:.4f}, MAE: {mae_lstm:.4f}, MAPE: {mape_lstm:.4f}%')

# Evaluate LSTM-Transformer Model
r2_lstm_transformer, rmse_lstm_transformer, mae_lstm_transformer, mape_lstm_transformer, pearson_lstm_transformer = evaluate_model(lstm_transformer_model, val_loader)
print(f'LSTM-Transformer Model - Pearson R: {pearson_lstm_transformer:.4f}, R2: {r2_lstm_transformer:.4f}, RMSE: {rmse_lstm_transformer:.4f}, MAE: {mae_lstm_transformer:.4f}, MAPE: {mape_lstm_transformer:.4f}%')


Transformer Model - Pearson R: -0.0547, R2: -0.4700, RMSE: 10.1865, MAE: 6.9782, MAPE: 815920700.0000%
DNN Model - Pearson R: nan, R2: -0.0001, RMSE: 8.4022, MAE: 6.6328, MAPE: 1969541800.0000%
LSTM Model - Pearson R: 0.0483, R2: -0.0000, RMSE: 8.4018, MAE: 6.6449, MAPE: 1980714400.0000%
LSTM-Transformer Model - Pearson R: 0.0770, R2: -0.0003, RMSE: 8.4029, MAE: 6.6846, MAPE: 2016501600.0000%


In [ ]:
# testdata, testlabel = test_loader.__iter__().__next__()
# print(model(testdata.unsqueeze(1)))
# print(testlabel)